# Introduction to ESG Bulk - Python

ESG stands for Environmental, Social and (Corporate) Governance data, accoring to WikiPedia, "the three central factors in measuring the sustainability and societal impact of an investment in a company or business". 

Refinitiv Data Platform (RDP) provides simple web based API access to a broad range of content.

Next, we are going to talk about ESG Bulk service - a service that provides the ESG Measures data with history for each of the companies in the ESG universe. This service is part of RDP family of services and is a RESTful web service, accessed via HTTP REST requests.

Learn more about ESG Bulk service via Refinitiv Data Platform APIs -> Documentation at:

https://developers.refinitiv.com/refinitiv-data-platform/refinitiv-data-platform-apis/docs

Within RDP family of service, ESG Bulk is part of Client File Store (CFS) - based section of service, find out more at:

https://developers.refinitiv.com/en/api-catalog/refinitiv-data-platform/refinitiv-data-platform-apis

Let us now focus on the programmatic interaction with ESG Bulk RDP service.

### Valid Credentials - Read From File

For this example, we have pre-stored a set of valid RDP crentials in a file and are going to retrieve them now

In [1]:
import requests, json, time, getopt, sys

credFile = open("..\creds\credFileHuman.txt","r")    # one per line
                                                #--- RDP MACHINE ID---
                                                #--- LONG PASSWORD---
                                                #--- GENERATED CLIENT ID---

USERNAME = credFile.readline().rstrip('\n')
PASSWORD = credFile.readline().rstrip('\n')
CLIENT_ID = credFile.readline().rstrip('\n')

credFile.close()

# Make sure that creds are read in correctly
#print("USERNAME="+str(USERNAME))
#print("PASSWORD="+str(PASSWORD))
#print("CLIENT_ID="+str(CLIENT_ID))

# Set Application Constants
RDP_AUTH_VERSION = "/v1"
RDP_ESG_BULK_VERSION = "/v1"
RDP_BASE_URL = "https://api.refinitiv.com"
RDP_ESG_BUCKET = "ESG"
CATEGORY_URL = "/auth/oauth2"
ENDPOINT_URL = "/token"
CLIENT_SECRET = ""
TOKEN_FILE = "token.txt"
SCOPE = "trapi"

### Define Token Handling and Obtain a Valid Token

Having a valid token is a pre-requisite to requesting of any RDP content, and will be passed into the next steps.

In [2]:
TOKEN_ENDPOINT = RDP_BASE_URL + CATEGORY_URL + RDP_AUTH_VERSION + ENDPOINT_URL

def _requestNewToken(refreshToken):
    if refreshToken is None:
        tData = {
            "username": USERNAME,
            "password": PASSWORD,
            "grant_type": "password",
            "scope": SCOPE,
            "takeExclusiveSignOnControl": "true"
        };
    else:
        tData = {
            "refresh_token": refreshToken,
            "grant_type": "refresh_token",
        };

    # Make a REST call to get latest access token
    response = requests.post(
        TOKEN_ENDPOINT,
        headers = {
            "Accept": "application/json"
        },
        data = tData,
        auth = (
            CLIENT_ID,
            CLIENT_SECRET
        )
    )
    
    if response.status_code != 200:
        raise Exception("Failed to get access token {0} - {1}".format(response.status_code, response.text));

    # Return the new token
    return json.loads(response.text);

def saveToken(tknObject):
    tf = open(TOKEN_FILE, "w+");
    print("Saving the new token");
    # Append the expiry time to token
    tknObject["expiry_tm"] = time.time() + int(tknObject["expires_in"]) - 10;
    # Store it in the file
    json.dump(tknObject, tf, indent=4)
    
def getToken():
    try:
        print("Reading the token from: " + TOKEN_FILE);
        # Read the token from a file
        tf = open(TOKEN_FILE, "r+")
        tknObject = json.load(tf);

        # Is access token valid
        if tknObject["expiry_tm"] > time.time():
            # return access token
            return tknObject["access_token"];

        print("Token expired, refreshing a new one...");
        tf.close();
        # Get a new token from refresh token
        tknObject = _requestNewToken(tknObject["refresh_token"]);

    except Exception as exp:
        print("Caught exception: " + str(exp))
        print("Getting a new token using Password Grant...");
        tknObject = _requestNewToken(None);

    # Persist this token for future queries
    saveToken(tknObject)
    print("Token is: " + tknObject["access_token"])
    # Return access token
    return tknObject["access_token"];

accessToken = getToken();
print("Have token now");

Reading the token from: token.txt
Token expired, refreshing a new one...
Caught exception: Failed to get access token 400 - {"error":"invalid_grant"   } 
Getting a new token using Password Grant...
Saving the new token
Token is: eyJ0eXAiOiJhdCtqd3QiLCJhbGciOiJSUzI1NiIsImtpZCI6ImRMdFd2Q0tCSC1NclVyWm9YMXFod2pZQ2t1eDV0V2ZSS2o4ME9vcjdUY28ifQ.eyJkYXRhIjoie1wiY2lwaGVydGV4dFwiOlwieE50YzNPbXVIUzN6ZzU1UDhkcjNjUUUwZHpwbUo4VGIxNm1iaFdOd2Z4SEhtajc3X1lheUtIdXN1U21YSUhHRzBocWEwWE54UG9rSDNoUm9ISXZKNWpmXzlnMi1SbHNKeGpwcnlmT1VqY0EtZFJBS2Rhb2YtSjVUQnhaSXRiS28yd3RvSkU1aC1uMnMxOGlaS1AySFk5QUp4b2ZRcWNtVmg4akNPMk1iS25Ic0RQMDVXWEM3dzhGdnNteVZfRFFrMGZkYjlUUVVvMGloSzZRMTd2a0ZqNElIV2hoTWRlcWxjOWhPbkxoX08tVDRDQXFKT0ZMMkE4VDdIaXN2V3hDaXJJS202Tk5va0ZwVjlYLWctU1BZTTg2cFJTc2Zfeno0QXk2alJEZmlCV1MtS1pGRHFJcnlsMTZoaFJTRl9rdGNQZU1aZGxUaWotTmc1Y2RjNHBnZDZwcmU1bmpwRkpLc1NEa3dtYzZKbmZwR1ViclRaX1VzeV9Tam92dzVCbUNyWTZkZG9DaDZFVE5ERmJMUnllakJVR3daNzVHUTFGX0p0WnNCWVEzQ1RnSU1GMzBLcVVTTDUzZ3Z0T3RJZUJJNXRvQl9JbDNuZnljYlVKbUl1aUV3

## Request Available File Sets

The purpose of ESG bulk service is obtaining ESG content in bulk.  The content is available as:

•	A full JSON data file containing history for all measures and all organizations.
•	A delta JSON data file that contains only incremental changes to the universe since last week. 

A customer can examine the available File Sets and is expected to:

•	Build the initial ESG representation with the full files
•	Apply delta, changes, as they become available
•	Fill a gap if the retrival was not completed and the content missed remains available

This step serves to verify the type of the file, for example:
•	ESGRawFullScheme
•	ESGScoresFull
•	ESGScoresWealthFull

In [9]:
FILESET_ENDPOINT = RDP_BASE_URL+'/file-store'+RDP_ESG_BULK_VERSION + '/file-sets?bucket='+ RDP_ESG_BUCKET
FILESET_ID = ''
WHICH_FILESET_ID_TO_STORE = 2   # 10 are returned per page

def requestFileSets(token, withNext, skipToken, attributes):   
    global FILESET_ENDPOINT
    global FILESET_ID
    global WHICH_FILESET_ID_TO_STORE   
    
    print("Obtaining FileSets in ESG Bucket...")
  
    querystring = {}
    payload = ""
    jsonfull = ""
    jsonpartial = ""
    
    headers = {
            'Content-Type': "application/json",
            'Authorization': "Bearer " + token,
            'cache-control': "no-cache"
    }

    if attributes:
        FILESET_ENDPOINT = FILESET_ENDPOINT + attributes
    if withNext:
        FILESET_ENDPOINT = FILESET_ENDPOINT + '&skipToken=' +skipToken
        
    response = requests.request("GET", FILESET_ENDPOINT, data=payload, headers=headers, params=querystring)
    
    if response.status_code != 200:
        if response.status_code == 401:   # error when token expired
                accessToken = getToken();     # token refresh on token expired
                headers['Authorization'] = "Bearer " + accessToken
                response = requests.request("GET", FILESET_ENDPOINT, data=payload, headers=headers, params=querystring)
         
    print('Raw response=');
    print(response);
    
    if response.status_code == 200:
        jsonFullResp = json.loads(response.text)
        print('Parsed json response=');
        print(json.dumps(jsonFullResp, indent=2));
        # We are going to store FileSet ID of the second File Set retrieved for future reference
        FILESET_ID = jsonFullResp['value'][WHICH_FILESET_ID_TO_STORE]['id']
        print('FILESET_ID stored is: '+str(FILESET_ID))
        return jsonFullResp; 
    else:
        return '';

jsonFullResp = requestFileSets(accessToken, False, '','');

Obtaining FileSets in ESG Bucket...
Reading the token from: token.txt
Token expired, refreshing a new one...
Caught exception: Failed to get access token 400 - {"error":"invalid_grant"   } 
Getting a new token using Password Grant...
Saving the new token
Token is: eyJ0eXAiOiJhdCtqd3QiLCJhbGciOiJSUzI1NiIsImtpZCI6ImRMdFd2Q0tCSC1NclVyWm9YMXFod2pZQ2t1eDV0V2ZSS2o4ME9vcjdUY28ifQ.eyJkYXRhIjoie1wiY2lwaGVydGV4dFwiOlwiaF9JcUd3TUNSNU9nSHRTNG40b0hxY1F4NXFzLWZKX0lCZjU0dWlPd0VjTUFweVg3N1Q0bHRqb0ZnVVc0aDZBaVhINDJHU0VUY0gwYmJyUlh5ME5Gb0dTZk9jLTB1MVN6Mjc0QWltUV9ZYW1YRFo3ZnhJdFhXSDI5ZWEzRlFhVXJ1aWR5Q1dzeHkxM01BWFZ2a3JvZzFkNV8yTnBabi1Dby1nUFNaNXppR3o4TjB6SHBBQ3U3NUJ4Yy1qckUwakZnbFlEM2tyVnVmNmlCVVBnTFlLVW9OSHE0T1YxOV9qVkhoeXl0dzhFbmhpT1ZfQnRxU0kxOVpPZE9mNGZSYTk4ajZBSi1mU0hyOWQtS21sdU5aTktzSFNHOHBDQmFJb1REYnc1LTZDN2NITVpuejBmNU5sMTRCM0FseFRnMTY5MzNNak1BUFcwSEVpWUIzZFRiOXRYc3JTdFVWSzU3OW1TOEJkSTc1ZURDU05iQnZCZDZQM0tZWXpvdm9qdlA0SngwYmIwQ1JiY0lMS3dNbVRDdThPN1VQeDRyWURCbmJuWEh4blhsT1RaQmhJWWdhaEREU09Nemprdncy

### Paginate Through the Available FileSets
(interrupt at any point)

In [ ]:
i = 1
while "@nextLink" in jsonFullResp: 
    print('<<< Iteraction: '+str(i)+' >>>  More exists: '+ jsonFullResp['@nextLink'] + ', skipToken is: ' + jsonFullResp['@nextLink'][-62:]+'\n')
    jsonFullResp = requestFileSets(accessToken, True, jsonFullResp['@nextLink'][-62:]);
    i+=1;
print('Last response without next=');
print(jsonFullResp);

<<< Iteraction: 1 >>>  More exists: /file-store/v1/file-sets?bucket=ESG&skipToken=ZmlsZXNldElkPTQzYmUtNDEwNS0zMGQyYzQ0Mi1iMTNmLTE0OTU2ODdkODcxZQ, skipToken is: ZmlsZXNldElkPTQzYmUtNDEwNS0zMGQyYzQ0Mi1iMTNmLTE0OTU2ODdkODcxZQ

Obtaining FileSets in ESG Bucket...
Raw response=
<Response [200]>
Parsed json response=
{
  "value": [
    {
      "id": "43e1-cf6f-ee34d6fa-9445-dc58220b1c2d",
      "name": "RFT-ESG-Raw-Current-SchemeB-Env-Delta-2020-10-25",
      "bucketName": "ESG",
      "packageId": "4cbb-e27e-318835e3-bad7-dee7a0ebc3b0",
      "attributes": [
        {
          "name": "ContentType",
          "value": "ESG Raw Current B"
        }
      ],
      "files": [
        "41b8-183f-0baf478d-99a9-630088800e44"
      ],
      "numFiles": 1,
      "availableFrom": "2020-10-25T16:37:32Z",
      "availableTo": "2020-11-25T16:37:32Z",
      "status": "READY",
      "created": "2020-10-25T16:37:32Z",
      "modified": "2020-10-25T16:37:40Z"
    },
    {
      "id": "4429-accc-5252b8c2-a

### Retrieve FileSets of Specific File Type (Filter By Attribute)
The file types may change over time, at present, the available FileSets are of types:

* ESG Raw Full A
* ESG Raw Full B
* ESG Raw Current A
* ESG Raw Current B
* ESG Sources
* ESG Raw Wealth Standard

* Symbology Cusip
* Symbology SEDOL
* Symbology Organization
* Symbology Instrument Quote


In [10]:
requestFileSets(accessToken, False, '','&attributes=ContentType:Symbology Cusip');

Obtaining FileSets in ESG Bucket...
Reading the token from: token.txt
Raw response=
<Response [200]>
Parsed json response=
{
  "value": [
    {
      "id": "4209-dd93-dbe4671d-b841-3662546bcdf0",
      "name": "RFT-ESG-Symbology-Cusip-Init-2020-11-19",
      "bucketName": "ESG",
      "packageId": "466c-c470-22a4cab3-8d0c-770cdfa5fc45",
      "attributes": [
        {
          "name": "ContentType",
          "value": "Symbology Cusip"
        }
      ],
      "files": [
        "4422-ec42-cb2bd8df-a0cd-a67e26ca24fd"
      ],
      "numFiles": 1,
      "availableFrom": "2020-11-19T10:29:12Z",
      "availableTo": "2020-12-19T10:29:11Z",
      "status": "READY",
      "created": "2020-11-19T10:29:12Z",
      "modified": "2020-11-19T10:29:14Z"
    },
    {
      "id": "435e-b1d8-6821efb7-ad57-eb8a44b60368",
      "name": "RFT-ESG-Symbology-Cusip-Init-2020-11-01",
      "bucketName": "ESG",
      "packageId": "466c-c470-22a4cab3-8d0c-770cdfa5fc45",
      "attributes": [
        {
       

### Retrieve Complete File Details of FileSet ID

In a previous step we have stored a FileSet ID that we are about to use for the demonstartion of this feature.

In [5]:
FILES_ENDPOINT = RDP_BASE_URL+'/file-store'+RDP_ESG_BULK_VERSION + '/files?filesetId='+ FILESET_ID
WHICH_FILE_ID_TO_STORE = 0
FILE_ID = ''
 
def requestFileDetails(token):   
    global FILES_ENDPOINT
    global FILE_ID
    print("Obtaining File details..." )
  
    querystring = {}
    payload = ""
    jsonfull = ""
    jsonpartial = ""
    
    headers = {
            'Content-Type': "application/json",
            'Authorization': "Bearer " + token,
            'cache-control': "no-cache"
    }
        
    response = requests.request("GET", FILES_ENDPOINT, data=payload, headers=headers, params=querystring)
    
    if response.status_code != 200:
        if response.status_code == 401:   # error when token expired
                accessToken = getToken();     # token refresh on token expired
                headers['Authorization'] = "Bearer " + accessToken
                response = requests.request("GET", FILES_ENDPOINT, data=payload, headers=headers, params=querystring)
         
    print('Raw response=');
    print(response);
    
    if response.status_code == 200:
        jsonFullResp = json.loads(response.text)
        print('Parsed json response=');
        print(json.dumps(jsonFullResp, indent=2));
        FILE_ID = jsonFullResp['value'][WHICH_FILE_ID_TO_STORE]['id']
        print('FILE_ID stored is: '+str(FILE_ID))
        return jsonFullResp; 
    else:
        return '';

jsonFullResp = requestFileDetails(accessToken);

Obtaining File details...
Reading the token from: token.txt
Token expired, refreshing a new one...
Saving the new token
Token is: eyJ0eXAiOiJhdCtqd3QiLCJhbGciOiJSUzI1NiIsImtpZCI6ImRMdFd2Q0tCSC1NclVyWm9YMXFod2pZQ2t1eDV0V2ZSS2o4ME9vcjdUY28ifQ.eyJkYXRhIjoie1wiY2lwaGVydGV4dFwiOlwic29UV0N2QVRNNFNBMFBNRHU3dm85RWVYYXZ2RERYQzF6c1hvelFnbkZWTTNYRXFLMUQxTFJ5N3R4eFVYWVF4Skw0ZmFYbVQ5b1pSekhFWU5oMnc4TDhNSzBvZ1hPbDQ2MG1Mdzd3Wjh1Uzh2U3FVMlhZN255TUlGTXE1WG1CSGd5dVZNaEJZNTR0YlVack5WR09QZFdPWVFLZkpzTld1SFV3S2gtQzdGMS1TLS1EaVBDQ2o5OThBVDJ5cVBwUUxXX2dVVUZhdHlfQ1NBTWRuWUdndTdHX09CWjJqOEpiYk9KWEtJYmtuLW5PMGkySzVXOG5oYzlZcE1sci14d3ZxTXEza05VNTRXY3lsa3IwOTZWOFdJZFRHbWg3NGdCNld4NE1nbmxUdGFHWkZMZlJwT1c0ejBEaVJwVGlXMEVYM0xHNmdmd09XNTRGVm95N0pXalBNTVNYZkRSYlpBa29FTWt4dkhXTWRwVmpZZm5GcEo3SGtmMkRfVlhQVHZyNHpJM2g0TUcxU29STHhwdnNrX2J1SnJ1dTZ6REFMM1pyZjdHbTdYaENjWU80dTdfa09vYzhIVFM3QTBLU2RlWnZCQlpCdkpIOVZSYS16aHhkTkM5b3FuN3pVR1doS3FTd2ZWME1zV29udWxkd3BVUVFwa29MUDUyT0R2WmRKb1NuaHRzZ05wdk5pc2h4YTZWc2dkOU5MaFE3VnhNaHF0bzV

###  Stream File via File Id using Redirect

In [6]:
import shutil

FILES_STREAM_ENDPOINT = RDP_BASE_URL+'/file-store'+RDP_ESG_BULK_VERSION + '/files/'+ FILE_ID+ '/stream'
 
def requestFileDownload(token):   
    global FILES_STREAM_ENDPOINT
    print("Obtaining File ... " + FILES_STREAM_ENDPOINT)
  
    filename = FILE_ID + '.gz'
    chunk_size = 1000
    
    headers = {
            'Authorization': 'Bearer ' + token,
            'cache-control': "no-cache",
            'Accept': '*/*'
    }
        
    response = requests.request("GET", FILES_STREAM_ENDPOINT, headers=headers, stream=True, allow_redirects=True)
    
    if response.status_code != 200:
        if response.status_code == 401:   # error when token expired
                accessToken = getToken();     # token refresh on token expired
                headers['Authorization'] = "Bearer " + accessToken
                response = requests.request("GET",FILES_STREAM_ENDPOINT, headers=headers, stream=True, allow_redirects=True)

         
    print('Response code=' + str(response.status_code));
    
    if response.status_code == 200:
        print('Processing...')
        with open(filename, 'wb') as fd:
            shutil.copyfileobj(response.raw, fd) 
#            for chunk in response.raw:
#                fd.write(chunk)
        print('Look for gzipped file named: '+ filename + ' in current directory')
        response.connection.close()
        
    return; 


requestFileDownload(accessToken);

Obtaining File ... https://api.refinitiv.com/file-store/v1/files/417b-7cea-2a5dfead-a17a-9604473dc9a1/stream
Reading the token from: token.txt
Response code=200
Processing...
Look for gzipped file named: 417b-7cea-2a5dfead-a17a-9604473dc9a1.gz in current directory


### Get File Location (Step 1 of 2)

In [7]:
import shutil

FILES_STREAM_ENDPOINT = RDP_BASE_URL+'/file-store'+RDP_ESG_BULK_VERSION + '/files/'+ FILE_ID+ '/stream?doNotRedirect=true'
DIRECT_URL = ''
 
def requestFileLocation(token):   
    
    global FILES_STREAM_ENDPOINT
    global DIRECT_URL
    
    print("Obtaining File ... " + FILES_STREAM_ENDPOINT)
  
    filename = FILE_ID + '.gz'
    chunk_size = 1000
    
    headers = {
            'Authorization': 'Bearer ' + token,
            'cache-control': "no-cache",
            'Accept': '*/*'
    }
        
    response = requests.request("GET", FILES_STREAM_ENDPOINT, headers=headers, stream=False, allow_redirects=False)
    
    if response.status_code != 200:
        if response.status_code == 401:   # error when token expired
                accessToken = getToken();     # token refresh on token expired
                headers['Authorization'] = "Bearer " + accessToken
                response = requests.request("GET",FILES_STREAM_ENDPOINT, headers=headers, stream=False, allow_redirects=False)

         
    print('Response code=' + str(response.status_code));
    
    if response.status_code == 200:
        jsonFullResp = json.loads(response.text)
        print('Parsed json response=');
        print(json.dumps(jsonFullResp, indent=2));
        DIRECT_URL = jsonFullResp['url'];
        print('File Direct URL is: '  +str(DIRECT_URL)+ '|||');
        
    return; 


requestFileLocation(accessToken);

Obtaining File ... https://api.refinitiv.com/file-store/v1/files/417b-7cea-2a5dfead-a17a-9604473dc9a1/stream?doNotRedirect=true
Reading the token from: token.txt
Response code=200
Parsed json response=
{
  "url": "https://a206464-prod-esg.s3.amazonaws.com/ESG_Sources/2020/11/15/RFT-ESG-Sources-Full-Init-2020-11-15-part00.jsonl.gz?x-eds-uuid=GENTC-25929&x-cfs-claimCheckId=417b-7cea-2a5dfead-a17a-9604473dc9a1&x-eds-requestId=1feea655-aaac-464d-bc02-7a363de8e9be&x-eds-appId=GE-A-01103867-3-603&x-event-external-name=cfs-claimCheck-download&X-Amz-Security-Token=IQoJb3JpZ2luX2VjEEkaCXVzLWVhc3QtMSJGMEQCICkxTY1QXkQ7beNIBdKwHV1nU70Pn8lRAZJvvXWChT35AiB3mlAs%2F29S3qtktWouUlTWyt3Eh8iCUf%2FEfA%2FkmiHCrSrBAwjC%2F%2F%2F%2F%2F%2F%2F%2F%2F%2F8BEAEaDDY0MjE1NzE4MTMyNiIMd4PAONoGgTpB6jrrKpUDPNt41c%2BXnLQghYdtiNB58bjUZU0tOWLN1SWMjLARS85OfOayVX01eqNoyg7h9e2KqkhJM3q%2FHlLCLNxLyHJZN97zZ%2BUl4QIyA7PGmtzTpfzjiwNDxlosnYqiV55snRhBJaIaQr040EeyCxvkfdGBtwGnlWzFzC%2FetW%2F7sI9dlOWkCzAbdrCqACXCTH7t4FqNhT6f3ufC71MX8V9Zc

### Download File From File Location (Step 2 of 2)

In [8]:
from urllib.parse import urlparse, parse_qs
def requestDirectFileDownload(token):   
    
    global DIRECT_URL
    print("Obtaining File from URL... " + DIRECT_URL)
    
    #Parse out URL parameters for submission into requests
    url_obj = urlparse(DIRECT_URL)
    parsed_params = parse_qs(url_obj.query)
    # extract the URL without query parameters
    parsed_url = url_obj._replace(query=None).geturl()

    response = requests.get(parsed_url, params=parsed_params,stream=True)
        
    if response.status_code != 200:
        if response.status_code == 401:   # error when token expired
                accessToken = getToken();     # token refresh on token expired
                headers['Authorization'] = "Bearer " + accessToken
                response = requests.get(parsed_url, params=query)

         
    print('Response code=' + str(response.status_code));        
  
    filename = FILE_ID + 'DIRECT.gz'    
    
    if response.status_code == 200:
        print('Processing...')
        with open(filename, 'wb') as fd:
            shutil.copyfileobj(response.raw, fd) 

        print('Look for gzipped file named: '+ filename + ' in current directory')
        response.connection.close()
        
    return; 


requestDirectFileDownload(accessToken);

Obtaining File from URL... https://a206464-prod-esg.s3.amazonaws.com/ESG_Sources/2020/11/15/RFT-ESG-Sources-Full-Init-2020-11-15-part00.jsonl.gz?x-eds-uuid=GENTC-25929&x-cfs-claimCheckId=417b-7cea-2a5dfead-a17a-9604473dc9a1&x-eds-requestId=1feea655-aaac-464d-bc02-7a363de8e9be&x-eds-appId=GE-A-01103867-3-603&x-event-external-name=cfs-claimCheck-download&X-Amz-Security-Token=IQoJb3JpZ2luX2VjEEkaCXVzLWVhc3QtMSJGMEQCICkxTY1QXkQ7beNIBdKwHV1nU70Pn8lRAZJvvXWChT35AiB3mlAs%2F29S3qtktWouUlTWyt3Eh8iCUf%2FEfA%2FkmiHCrSrBAwjC%2F%2F%2F%2F%2F%2F%2F%2F%2F%2F8BEAEaDDY0MjE1NzE4MTMyNiIMd4PAONoGgTpB6jrrKpUDPNt41c%2BXnLQghYdtiNB58bjUZU0tOWLN1SWMjLARS85OfOayVX01eqNoyg7h9e2KqkhJM3q%2FHlLCLNxLyHJZN97zZ%2BUl4QIyA7PGmtzTpfzjiwNDxlosnYqiV55snRhBJaIaQr040EeyCxvkfdGBtwGnlWzFzC%2FetW%2F7sI9dlOWkCzAbdrCqACXCTH7t4FqNhT6f3ufC71MX8V9ZcsFtWP%2B5p1C7xmzstC1NYX%2BzHPAVk5C7x9K04zJmdY0idZo8bxNkU2k46MAGKG%2B6MQfOZ%2FGrhEn%2FMqPjKRLpvmsgkvpYMPeLkUunUHKO6J%2BNLgbsCkL5oogc6DEnS1a%2FmGWyQ8jPd5832%2F9U4h%2B8TsWTTNhDzSqJJ2KKziosIA